<a href="https://colab.research.google.com/github/AliaksandrSiarohin/first-order-model/blob/master/demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Demo for paper "First Order Motion Model for Image Animation"

This notebook uses the source code provided with the paper [First Order Motion Model for Image Animation](https://papers.nips.cc/paper/8935-first-order-motion-model-for-image-animation) by Aliaksandr Siarohin, [Stéphane Lathuilière](http://stelat.eu), [Sergey Tulyakov](http://stulyakov.com), [Elisa Ricci](http://elisaricci.eu/) and [Nicu Sebe](http://disi.unitn.it/~sebe/). The original code is available here: https://github.com/AliaksandrSiarohin/first-order-model.

In [ ]:
# Clone my forked repo that contains demo artifacts
!git clone https://github.com/ryanloney/first-order-model.git

In [ ]:
# Checkout the demo branch
!git checkout demo

**Load driving video and source image**

In [1]:
import imageio
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from skimage.transform import resize
from IPython.display import HTML
import warnings
warnings.filterwarnings("ignore")

source_image = imageio.imread('data/kahlo.png')
reader = imageio.get_reader('data/ryan.mp4')


# Resize image and video to 256x256
source_image = resize(source_image, (256, 256))[..., :3]

fps = reader.get_meta_data()['fps']
driving_video = []
try:
    for im in reader:
        driving_video.append(im)
except RuntimeError:
    pass
reader.close()

driving_video = [resize(frame, (256, 256))[..., :3] for frame in driving_video]

def display(source, driving, generated=None):
    fig = plt.figure(figsize=(8 + 4 * (generated is not None), 6))

    ims = []
    for i in range(len(driving)):
        cols = [source]
        cols.append(driving[i])
        if generated is not None:
            cols.append(generated[i])
        im = plt.imshow(np.concatenate(cols, axis=1), animated=True)
        plt.axis('off')
        ims.append([im])

    ani = animation.ArtistAnimation(fig, ims, interval=50, repeat_delay=1000)
    plt.close()
    return ani
    
# HTML(display(source_image, driving_video).to_html5_video())

**Download the model**

In [11]:
!wget -P data/ https://face-animation.s3-us-west-2.amazonaws.com/vox-cpk.pth.tar

--2021-02-28 19:01:01--  https://face-animation.s3-us-west-2.amazonaws.com/vox-cpk.pth.tar
Resolving face-animation.s3-us-west-2.amazonaws.com (face-animation.s3-us-west-2.amazonaws.com)... 52.218.218.145
Connecting to face-animation.s3-us-west-2.amazonaws.com (face-animation.s3-us-west-2.amazonaws.com)|52.218.218.145|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 728766691 (695M) [application/x-tar]
Saving to: ‘data/vox-cpk.pth.tar’

vox-cpk.pth.tar     100%[===================>] 695.01M  81.1MB/s    in 9.2s    

2021-02-28 19:01:10 (75.7 MB/s) - ‘data/vox-cpk.pth.tar’ saved [728766691/728766691]



**Create a model and load checkpoints**

In [2]:
from demo import load_checkpoints
generator, kp_detector = load_checkpoints(config_path='config/vox-256.yaml', 
                            checkpoint_path='data/vox-cpk.pth.tar')

**Perform image animation**

In [4]:
from demo import make_animation
from skimage import img_as_ubyte

predictions = make_animation(source_image, driving_video, generator, kp_detector, relative=True)

#save resulting video
imageio.mimsave('generated_kahlo.mp4', [img_as_ubyte(frame) for frame in predictions], fps=fps)
#video can be downloaded from /content folder

HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 1134/1134 [00:30<00:00, 37.73it/s]


In [4]:
# Try another input image
source_image = imageio.imread('data/einstein.png')

# Resize source image
source_image = resize(source_image, (256, 256))[..., :3]

predictions = make_animation(source_image, driving_video, generator, kp_detector, relative=True,
                             adapt_movement_scale=True)

# Save resulting video
imageio.mimsave('generated_einstein.mp4', [img_as_ubyte(frame) for frame in predictions], fps=fps)

HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 1134/1134 [00:29<00:00, 37.99it/s]


In [ ]:
# Try another input image
source_image = imageio.imread('data/gandhi.png')
source_image = resize(source_image, (256, 256))[..., :3]

predictions = make_animation(source_image, driving_video, generator, kp_detector, relative=True,
                             adapt_movement_scale=True)

imageio.mimsave('generated_gandhi.mp4', [img_as_ubyte(frame) for frame in predictions], fps=fps)

HTML(display(source_image, driving_video, predictions).to_html5_video())

## Running on your data
**First, we need to capture video from your laptop or PC camera.** See instructions for [Windows](https://answers.microsoft.com/en-us/windows/forum/windows_10-hardware/how-to-record-video-with-webcam-windows-10/a65fae0f-86d3-4a82-999d-5003a2c78ad8#) and [Mac](https://support.apple.com/guide/quicktime-player/record-a-movie-qtp356b55534/mac).

**Next, we need to crop a face from both the source image and video.** A simple graphic editor like preview (Mac) or Paint (Windows) can be used for cropping the image. Cropping from video is more complicated. You can use ffpmeg for this.

In [29]:
# you can replace camera.mov with your own video or just run this cell to test with my video
!ffmpeg -i data/camera.mov -ss 00:00:00.50 -t 00:00:19 -filter:v "crop=1000:1000" -async 1 driver.mp4

ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lib

**More about video preprocessing in https://github.com/AliaksandrSiarohin/video-preprocessing** 

In [3]:
# Run this to use the cropped video from the previous step
source_image = imageio.imread('data/monroe.png')
driving_video = imageio.mimread('driver.mp4', memtest=False)

# Resize image and video to 256x256
source_image = resize(source_image, (256, 256))[..., :3]
driving_video = [resize(frame, (256, 256))[..., :3] for frame in driving_video]

predictions = make_animation(source_image, driving_video, generator, kp_detector, relative=True,
                             adapt_movement_scale=True)

#save resulting video
imageio.mimsave('generated.mp4', [img_as_ubyte(frame) for frame in predictions], fps=fps)

HTML(display(source_image, driving_video, predictions).to_html5_video())

100%|██████████| 1134/1134 [00:29<00:00, 38.09it/s]
